## Analyse du datadrif avec Evidently

L'analyse du datadrift  est un processus essentiel pour surveiller, maintenir et assurer la qualité des modèles ML en production. Cela permet de garantir leur performance continue face à des données changeantes dans un environnement réel.

In [1]:
import pandas as pd
import numpy as np
import time, pickle
from sklearn.datasets import fetch_california_housing
import xgboost as xgb
from xgboost import XGBClassifier
from evidently import ColumnMapping

from evidently.report import Report
from evidently.metrics.base_metric import generate_column_metrics
from evidently.metric_preset import DataDriftPreset, TargetDriftPreset, DataQualityPreset, RegressionPreset
from evidently.metrics import *

from evidently.test_suite import TestSuite
from evidently.tests.base_test import generate_column_tests
from evidently.test_preset import DataStabilityTestPreset, NoTargetPerformanceTestPreset, RegressionTestPreset
from evidently.tests import *

In [2]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

Pour notre cas nous allons utiliser les dataframes application_train et application_test pour faire l'analyse.

In [3]:
application_train = pd.read_csv("/Users/soneitaraherimalala/Desktop/P7/Projet+Mise+en+prod+-+home-credit-default-risk/application_train.csv")
application_test = pd.read_csv("/Users/soneitaraherimalala/Desktop/P7/Projet+Mise+en+prod+-+home-credit-default-risk/application_test.csv")

In [4]:
application_train.shape

(307511, 122)

In [5]:
application_test.shape

(48744, 121)

Tout d'abord, nous allons traiter les variables catégorielles avec la méthode pd.get_dummies pour les tranformer en binaire.

In [6]:
categorical_col = [col for col in application_train.columns if application_train[col].dtype == 'object']
categorical_cols = [col for col in application_test.columns if application_test[col].dtype == 'object']

In [7]:
train_data = pd.get_dummies(application_train, columns=categorical_col)
test_data = pd.get_dummies(application_test, columns=categorical_cols)

In [8]:
train_data.shape

(307511, 246)

In [9]:
test_data.shape

(48744, 242)

Après, nous allons enlever les colonnes qui différencient les deux dataframes, pour avoir les mêmes colonnes.

In [10]:
# Obtenir les colonnes présentes dans df1 mais pas dans df2
columns_to_drop = [col for col in train_data.columns if col not in test_data.columns]

# Supprimer les colonnes en surplus dans df1
train_data = train_data.drop(columns=columns_to_drop, axis=1)

In [11]:
train_data.shape

(307511, 242)

In [12]:
test_data.shape

(48744, 242)

Puis, nous définissons les dataframes de référence et current pour faire l'analyse. Pour écourter le temps de traitement, nous allons prendre uniquement les 1000 premiers lignes de nos dataframes.

In [13]:
reference=train_data.head(1000)
current=test_data.head(1000)

Ensuite, nous allons faire le datadrift. et nous obtenons le fichier html correspondant.

In [15]:
report = Report(metrics=[
    DataDriftPreset(), 
])

report.run(reference_data=reference, current_data=current)
report

In [17]:
report.save_html("datadrift.html")

In [2]:
import json

print(json.__version__)


2.0.9
